<a href="https://colab.research.google.com/github/Ashish-Soni08/Playground/blob/main/DTC_zoomcamp_Q%26A_Challenge_Ashish_Soni.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Problem Statement

**DataTalks.Club**, a hub for data science learning, generates a significant amount of Q&A data through its courses. This competition aims to harness this data to create models that can automate the matching of questions to answers, **enhancing educational resources and learner experiences**.

## Objective
The primary goal is to develop a model that can accurately match a given question to its correct answer using the provided dataset.

## Impact
Successful models from this competition could revolutionize how **DataTalks.Club**  manages the content, making it easier for learners to find the answers.

## Evaluation
**Accuracy**: The accuracy metric will assess the proportion of correctly matched question-answer pairs. Higher accuracy indicates better performance of the model

## Instructions
- Harness your data science skills to explore, analyze, and create models that excel in question-answer pairing
- Baseline using all-MiniLM-L6-v2 sentence transformer and cosine similarity to find the matching answer_id for each question

# Install

In [1]:
!pip install -qqq kaggle langchain langchain-openai langchain-together langchain_mistralai llama-index Pillow sentence-transformers transformers fastapi kaleido python-multipart uvicorn cohere

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 803.6/803.6 kB 7.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 15.9/15.9 MB 28.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 132.8/132.8 kB 12.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 92.0/92.0 kB 7.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 79.9/79.9 MB 10.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 45.7/45.7 kB 2.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 60.7/60.7 kB 5.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 52.1/52.1 kB 4.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.6/1.6 MB 31.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 235.9/235.9 kB 20.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 54.0/54.0 kB 4.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 225.1/225.1 kB 19.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━

## Imports

In [2]:
import os

from google.colab import data_table

import numpy as np

import pandas as pd

import torch

from tqdm.auto import tqdm

from sentence_transformers import SentenceTransformer, util

from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics import accuracy_score
from sklearn.preprocessing import StandardScaler
from sklearn.metrics.pairwise import cosine_similarity
# Embeddings from different Providers through the Langchain framework
## Langchain
from langchain_community.embeddings import CohereEmbeddings
from langchain_community.embeddings import JinaEmbeddings
from langchain_mistralai import MistralAIEmbeddings
from langchain_openai import OpenAIEmbeddings
from langchain_together.embeddings import TogetherEmbeddings
from langchain_community.embeddings import VoyageEmbeddings
## LlamaIndex
from llama_index.embeddings import OpenAIEmbedding

from typing import Dict, List

import warnings
warnings.filterwarnings("ignore")

In [3]:
pd.set_option('display.max_rows', None)  # Shows all rows
pd.set_option('display.max_columns', None)  # Shows all columns
pd.set_option('display.width', None)  # Auto-detect the display width
pd.set_option('display.max_colwidth', None)  # Display full width of columns

In [4]:
# Use GPU if available
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Available device: {device}")

Available device: cuda


In [5]:
from google.colab import userdata

# Cohere
COHERE_API_KEY = userdata.get('cohere_api')

# Jina
JINA_API_KEY = userdata.get('jina_embed_api')

# Kaggle
KAGGLE_USERNAME = userdata.get('kaggle_username')
KAGGLE_API_KEY = userdata.get('kaggle_api_key')

# MISTRAL
MISTRAL_API_KEY = userdata.get('mistral_api')

# OPENAI
OPENAI_API_KEY = userdata.get('openai_api')

# Together
TOGETHER_API_KEY = userdata.get('togetherai_api')

# Voyage
VOYAGE_API_KEY = userdata.get('voyage_api')

print("All APIs and ENDPOINTS are available for Access! Let's get Started :)")

All APIs and ENDPOINTS are available for Access! Let's get Started :)


# DATA

In [ ]:
from google.colab import files

# Kaggle Setup

kaggle_file = "~/.kaggle/kaggle.json"

if not os.path.exists('~/.kaggle'):
  !mkdir ~/.kaggle

if not os.path.isfile(kaggle_file):
  files.upload() # produces a prompt
  # After uploading kaggle.json
  !cp kaggle.json ~/.kaggle/
  !chmod 600 ~/.kaggle/kaggle.json

Saving kaggle.json to kaggle.json


In [ ]:
# Check if it works
!kaggle datasets list

ref                                                                title                                               size  lastUpdated          downloadCount  voteCount  usabilityRating  
-----------------------------------------------------------------  -------------------------------------------------  -----  -------------------  -------------  ---------  ---------------  
nelgiriyewithana/apple-quality                                     Apple Quality                                      170KB  2024-01-11 14:31:07           6150        144  1.0              
hummaamqaasim/jobs-in-data                                         Jobs and Salaries in Data Science                   76KB  2023-12-25 20:03:32          12504        228  1.0              
emirhanai/city-happiness-index-2024                                City Happiness Index - 2024                          8KB  2024-01-22 00:41:50           1475         32  1.0              
shiivvvaam/revenue-of-top-companies-in-india      

In [ ]:
# Download Data from Kaggle
if not os.path.exists('content/data/train_questions.csv'):
  !kaggle competitions download -c dtc-zoomcamp-qa-challenge
  !mkdir data
  !unzip dtc-zoomcamp-qa-challenge.zip -d data > /dev/null
  !rm dtc-zoomcamp-qa-challenge.zip

 97% 5.00M/5.15M [00:00<00:00, 47.5MB/s]
100% 5.15M/5.15M [00:00<00:00, 48.6MB/s]


In [ ]:
!ls data

 attachments		      test_answers.csv	   train_answers.csv
'sample_submission (1).csv'   test_questions.csv   train_questions.csv


## LOAD DATA

In [ ]:
DATA_PATH = '/content/data'

train_questions_df = pd.read_csv(f'{DATA_PATH}/train_questions.csv')
train_answers_df = pd.read_csv(f'{DATA_PATH}/train_answers.csv')
test_questions_df = pd.read_csv(f'{DATA_PATH}/test_questions.csv')
test_answers_df = pd.read_csv(f'{DATA_PATH}/test_answers.csv')

## EDA for Training Data

### Observations after EDA:

1. Duplicate Question IDs: The dataset contains duplicate question_id entries, specifically 3 instances where question_id is repeated.

2. Column Uniqueness:

- Columns like `course_question`, `year_question`, `course_answer`, and `year_answer` have only 2 unique values, indicating the courses `Machine Learning Zoomcamp`, `Data Engineering Zoomcamp` and the years `2021` and `2022`.

- The attachments_files column has 25 unique values but also a significant number of missing values (374 out of 399), suggesting limited utility in analysis.

3. Duplicate Rows: There are duplicate rows in the dataset, particularly where question_id is `647840, 172850, and 631555`. These duplicates seem to represent the same question being asked or answered multiple times, with minor variations in the candidate answers and answers.

### Decisions for Data Preprocessing
Based on the observations, the following decisions were made for data preprocessing:

1. Remove attachments_files Column: This column will be removed due to the high number of missing values and its limited contribution to the overall informative value of the dataset.

2. Resolve Duplicate `question_id` Entries: For each duplicate question_id, only the last row will be kept. This decision was made based on the observation that the last entry tends to have the most complete and relevant answer, especially noticeable for `question_id` `647840`. This approach ensures that the dataset represents the most comprehensive information available for each question.

- Specifically for `question_id` `647840`, the last row was kept as it contained a more comprehensive answer compared to the previous entry.
- The same approach will be applied to `question_id` `172850 and 631555`

In [ ]:
def column_analysis(df: pd.DataFrame, column_name: str) -> None:
    """
    Performs basic analysis on a specified column of a pandas DataFrame and prints the results.

    Args:
    df (pd.DataFrame): The DataFrame containing the column to be analyzed.
    column_name (str): The name of the column to analyze.

    The function prints:
      - 'column_name': The name of the column.
      - 'type': The data type of the column.
      - 'unique_count': The number of unique values in the column.
      - 'missing_values': The number of missing (NaN, None, etc.) values in the column.
      - 'duplicate_values': The number of duplicate values in the column.
    If the specified column name does not exist in the DataFrame, a message indicating this is printed.
    """
    if column_name in df.columns:
        analysis = {
            'column_name': column_name,
            'type': df[column_name].dtype,
            'unique_count': df[column_name].nunique(),
            'missing_values': df[column_name].isnull().sum(),
            'duplicate_values': df[column_name].shape[0] - df[column_name].nunique()
        }
        for key, value in analysis.items():
            print(f"{key}: {value}")
    else:
        print(f"The column '{column_name}' does not exist in the DataFrame.")

In [ ]:
def print_column_values(df: pd.DataFrame, column_name: str) -> None:
    """
    Prints the unique values of a specified column in a pandas DataFrame.

    Args:
    df (pd.DataFrame): The DataFrame containing the column.
    column_name (str): The name of the column for which to print unique values.

    Returns:
    None. Prints the unique values of the column to the console.
    """
    if column_name in df.columns:
        unique_values = df[column_name].unique()
        unique_values_list = unique_values.tolist()
        print(f"Unique values in '{column_name}': {unique_values_list}")
    else:
        print(f"The column '{column_name}' does not exist in the DataFrame.")

### Training Data

In [ ]:
print(f"Rows and Columns -> {train_questions_df.shape}")
print(f"Rows and Columns -> {train_answers_df.shape}")

Rows and Columns -> (397, 6)
Rows and Columns -> (397, 5)


In [ ]:
data_table.DataTable(train_questions_df, include_index=False, num_rows_per_page=10)

In [ ]:
data_table.DataTable(train_answers_df, include_index=False, num_rows_per_page=3)

In [ ]:
# Let's merge the train questions and answers in one dataframe
train_merged_df = pd.merge(
    train_questions_df, train_answers_df, on='answer_id', how='inner', suffixes=('_question', '_answer')
)

In [ ]:
data_table.DataTable(train_merged_df, include_index=False, num_rows_per_page=3)

In [ ]:
print(f"Rows and Columns -> {train_merged_df.shape}")

Rows and Columns -> (399, 10)


In [ ]:
for column in train_merged_df.columns:
  print()
  column_analysis(train_merged_df, column)
  print()
  print(25 * '*')


column_name: question_id
type: int64
unique_count: 396
missing_values: 0
duplicate_values: 3

*************************

column_name: question
type: object
unique_count: 396
missing_values: 0
duplicate_values: 3

*************************

column_name: course_question
type: object
unique_count: 2
missing_values: 0
duplicate_values: 397

*************************

column_name: year_question
type: int64
unique_count: 2
missing_values: 0
duplicate_values: 397

*************************

column_name: candidate_answers
type: object
unique_count: 397
missing_values: 0
duplicate_values: 2

*************************

column_name: answer_id
type: int64
unique_count: 396
missing_values: 0
duplicate_values: 3

*************************

column_name: answer
type: object
unique_count: 396
missing_values: 0
duplicate_values: 3

*************************

column_name: course_answer
type: object
unique_count: 2
missing_values: 0
duplicate_values: 397

*************************

column_name: year_answ

In [ ]:
columns_list = ['course_question', 'year_question', 'course_answer', 'year_answer']
for column in columns_list:
  print_column_values(train_merged_df, column)
  print()

Unique values in 'course_question': ['Machine Learning Zoomcamp', 'Data Engineering Zoomcamp']

Unique values in 'year_question': [2021, 2022]

Unique values in 'course_answer': ['Machine Learning Zoomcamp', 'Data Engineering Zoomcamp']

Unique values in 'year_answer': [2021, 2022]



In [ ]:
# Checking for duplicate rows in the DataFrame
duplicate_rows = train_merged_df[train_merged_df.duplicated('question_id')]

# Number of duplicate rows
num_duplicate_rows = duplicate_rows.shape[0]
num_duplicate_rows

3

In [ ]:
# Find duplicate question_ids
duplicate_question_df = train_merged_df[train_merged_df.duplicated('question_id', keep=False)]

# Display the duplicate question_ids
data_table.DataTable(duplicate_question_df, include_index=False, num_rows_per_page=10)

In [ ]:
# Drop Column -> attachments_files
train_dataset = train_merged_df.drop(columns=['attachments_files'])

print(f"Rows and Columns -> {train_dataset.shape}")

Rows and Columns -> (399, 9)


In [ ]:
train_dataset.columns

Index(['question_id', 'question', 'course_question', 'year_question', 'candidate_answers',
       'answer_id', 'answer', 'course_answer', 'year_answer'],
      dtype='object')

In [ ]:
# Drop duplicates
train_dataset = train_dataset.drop_duplicates(subset = 'question_id', keep = 'last')

print(f"Shape of the Dataset after dropping duplicates -> {train_dataset.shape}") # 396

Shape of the Dataset after dropping duplicates -> (396, 9)


In [ ]:
train_dataset["candidate_answers"] = train_dataset["candidate_answers"].str.split(",")

In [ ]:
train_dataset.to_csv("training_dataset.csv", index = False)

In [ ]:
data_table.DataTable(train_dataset, include_index=False, num_rows_per_page=2)

## EDA for Test Data


`year`: 2022, 2023

`course`: Data Engineering Zoomcamp, Machine Learning Zoomcamp



### Test Data

In [ ]:
print(f"Rows and Columns -> {test_questions_df.shape}")
print(f"Rows and Columns -> {test_answers_df.shape}")

Rows and Columns -> (516, 5)
Rows and Columns -> (516, 5)


In [ ]:
## Test Dataset
data_table.DataTable(test_questions_df, include_index=False, num_rows_per_page=10)

In [ ]:
for column in test_questions_df.columns:
  print()
  column_analysis(test_questions_df, column)
  print()
  print(25 * '*')


column_name: question_id
type: int64
unique_count: 514
missing_values: 0
duplicate_values: 2

*************************

column_name: question
type: object
unique_count: 514
missing_values: 0
duplicate_values: 2

*************************

column_name: course
type: object
unique_count: 2
missing_values: 0
duplicate_values: 514

*************************

column_name: year
type: int64
unique_count: 2
missing_values: 0
duplicate_values: 514

*************************

column_name: candidate_answers
type: object
unique_count: 516
missing_values: 0
duplicate_values: 0

*************************


In [ ]:
test_columns = ['course', 'year']
for column in test_columns:
  print_column_values(test_questions_df, column)
  print()

Unique values in 'course': ['Data Engineering Zoomcamp', 'Machine Learning Zoomcamp']

Unique values in 'year': [2023, 2022]



In [ ]:
data_table.DataTable(test_answers_df, include_index=False, num_rows_per_page=2)

In [ ]:
for column in test_answers_df.columns:
  print()
  column_analysis(test_answers_df, column)
  print()
  print(25 * '*')


column_name: answer_id
type: int64
unique_count: 515
missing_values: 0
duplicate_values: 1

*************************

column_name: answer
type: object
unique_count: 515
missing_values: 0
duplicate_values: 1

*************************

column_name: course
type: object
unique_count: 2
missing_values: 0
duplicate_values: 514

*************************

column_name: year
type: int64
unique_count: 2
missing_values: 0
duplicate_values: 514

*************************

column_name: attachments_files
type: object
unique_count: 8
missing_values: 508
duplicate_values: 508

*************************


In [ ]:
for column in test_columns:
  print_column_values(test_answers_df, column)
  print()

Unique values in 'course': ['Data Engineering Zoomcamp', 'Machine Learning Zoomcamp']

Unique values in 'year': [2023, 2022]



In [ ]:
# Checking for duplicate rows in the DataFrame
duplicate_rows = test_questions_df[test_questions_df.duplicated('question_id')]

# Number of duplicate rows
num_duplicate_rows = duplicate_rows.shape[0]
num_duplicate_rows

2

In [ ]:
# Find duplicate question_ids
duplicate_question_test_df = test_questions_df[test_questions_df.duplicated('question_id', keep=False)]

# Display the duplicate question_ids
data_table.DataTable(duplicate_question_test_df, include_index=False, num_rows_per_page=10)

In [ ]:
# Drop Duplicates
test_questions_dataset = test_questions_df.drop_duplicates(subset = 'question_id', keep = 'last')
print(f"Shape of the Dataset after dropping duplicates -> {test_questions_dataset.shape}") # 514

Shape of the Dataset after dropping duplicates -> (514, 5)


In [ ]:
test_questions_dataset["candidate_answers"] = test_questions_dataset["candidate_answers"].str.split(",")

In [ ]:
data_table.DataTable(test_questions_dataset, include_index=False, num_rows_per_page=3)

In [ ]:
test_questions_dataset.to_csv('test_questions_dataset.csv', index=False)

In [ ]:
# Checking for duplicate rows in the DataFrame
duplicate_rows = test_answers_df[test_answers_df.duplicated('answer_id')]

# Number of duplicate rows
num_duplicate_rows = duplicate_rows.shape[0]
num_duplicate_rows

1

In [ ]:
# Find duplicate question_ids
duplicate_answers_test_df = test_answers_df[test_answers_df.duplicated('answer_id', keep=False)]

# Display the duplicate question_ids
data_table.DataTable(duplicate_answers_test_df, include_index=False, num_rows_per_page=10)

In [ ]:
# Drop Duplicates
test_answers_dataset = test_answers_df.drop_duplicates(subset = 'answer_id', keep = 'last')
print(f"Shape of the Dataset after dropping duplicates -> {test_answers_dataset.shape}") # 514

Shape of the Dataset after dropping duplicates -> (515, 5)


In [ ]:
# Drop Column -> attachments_files
test_answers_dataset = test_answers_dataset.drop(columns=['attachments_files'])

print(f"Rows and Columns -> {test_answers_dataset.shape}")

Rows and Columns -> (515, 4)


In [ ]:
test_answers_dataset.to_csv('test_answers_dataset.csv', index=False)

In [6]:
train_dataset = pd.read_csv("/content/training_dataset.csv")

In [11]:
train_dataset.shape

(396, 9)

In [8]:
test_questions_dataset = pd.read_csv("/content/test_questions_dataset.csv")

In [12]:
test_questions_dataset.shape

(514, 5)

In [9]:
test_answers_dataset = pd.read_csv("/content/test_answers_dataset.csv")

In [10]:
test_answers_dataset.shape

(515, 4)

# MODELS

In [ ]:
# Models to get Embeddings

## Hugging Face
# Baseline - MiniLM
MINILM = 'all-MiniLM-L6-v2'
minilm_model = SentenceTransformer(MINILM)
print(f"{MINILM} -> model is Ready")
print(30 * '#')

# BGE
BGE = 'BAAI/bge-large-en-v1.5'
bge_model = SentenceTransformer(BGE)
print(f"{BGE} -> model is Ready")
print(30 * '#')

modules.json:   0%|          | 0.00/349 [00:00<?, ?B/s]

config_sentence_transformers.json:   0%|          | 0.00/116 [00:00<?, ?B/s]

README.md:   0%|          | 0.00/10.6k [00:00<?, ?B/s]

sentence_bert_config.json:   0%|          | 0.00/53.0 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/612 [00:00<?, ?B/s]

...

vocab.txt:   0%|          | 0.00/232k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/711k [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/125 [00:00<?, ?B/s]

1_Pooling/config.json:   0%|          | 0.00/191 [00:00<?, ?B/s]

BAAI/bge-large-en-v1.5 -> model is Ready
##############################


In [ ]:
%%time
minilm_model.to(device) # Move model to GPU

print("Training Dataset")
minilm_train_q_emb = minilm_model.encode(train_dataset["question"].values, show_progress_bar = True)
print("Created question embedings using Mini-LM for Training Dataset")
print(30 * '#')

minilm_train_ans_emb = minilm_model.encode(train_dataset["answer"].values, show_progress_bar = True)
print("Created answer embedings using Mini-LM for Training Dataset")
print(30 * '#')

print(f"Shape of Embeddings for Questions using Mini-LM model in Training Dataset -> {minilm_train_q_emb.shape}")
print(f"Shape of Embeddings for Answers using Mini-LM model in Training Dataset -> {minilm_train_ans_emb.shape}")
print()
print(50 * '#')

print("Test Dataset")
minilm_test_q_emb = minilm_model.encode(test_questions_dataset["question"].values, show_progress_bar = True)
print("Created question embedings using Mini-LM for Test Dataset")
print(30 * '#')

minilm_test_ans_emb = minilm_model.encode(test_answers_dataset["answer"].values, show_progress_bar = True)
print("Created answer embedings using Mini-LM for Test Dataset")
print(30 * '#')


print(f"Shape of Embeddings for Questions using Mini-LM model in Test Dataset -> {minilm_test_q_emb.shape}")
print(f"Shape of Embeddings for Answers using Mini-LM model in Test Dataset -> {minilm_test_ans_emb.shape}")

Training Dataset


Batches:   0%|          | 0/13 [00:00<?, ?it/s]

Created question embedings using Mini-LM for Training Dataset
##############################


Batches:   0%|          | 0/13 [00:00<?, ?it/s]

Created answer embedings using Mini-LM for Training Dataset
##############################
Shape of Embeddings for Questions using Mini-LM model in Training Dataset -> (396, 384)
Shape of Embeddings for Answers using Mini-LM model in Training Dataset -> (396, 384)

##################################################
Testing Dataset


Batches:   0%|          | 0/17 [00:00<?, ?it/s]

Created question embedings using Mini-LM for Test Dataset
##############################


Batches:   0%|          | 0/17 [00:00<?, ?it/s]

Created answer embedings using Mini-LM for Test Dataset
##############################
Shape of Embeddings for Questions using Mini-LM model in Test Dataset -> (514, 384)
Shape of Embeddings for Answers using Mini-LM model in Test Dataset -> (515, 384)
CPU times: user 2.98 s, sys: 23.3 ms, total: 3 s
Wall time: 2.71 s


In [ ]:
type(minilm_train_q_emb)

numpy.ndarray

In [ ]:
%%time
bge_model.to(device) # Move model to GPU
print("Training Dataset")
bge_train_q_embed = bge_model.encode(train_dataset["question"].values, show_progress_bar = True)
print("Created question embedings using BGE")
print(30 * '#')

bge_train_ans_embed = bge_model.encode(train_dataset["answer"].values, show_progress_bar = True)
print("Created answer embedings using BGE")
print(30 * '#')


print(f"Shape of Embeddings for Questions using BGE model in Training Dataset -> {bge_train_q_embed.shape}")
print(f"Shape of Embeddings for Answers using BGE model  in Training Dataset-> {bge_train_ans_embed.shape}")
print()
print(50 * '#')

print("Test Dataset")
bge_test_q_emb = bge_model.encode(test_questions_dataset["question"].values, show_progress_bar = True)
print("Created question embedings using BGE for Test Dataset")
print(30 * '#')

bge_test_ans_emb = bge_model.encode(test_answers_dataset["answer"].values, show_progress_bar = True)
print("Created answer embedings using BGE for Test Dataset")
print(30 * '#')


print(f"Shape of Embeddings for Questions using Mini-LM model in Test Dataset -> {bge_test_q_emb.shape}")
print(f"Shape of Embeddings for Answers using Mini-LM model in Test Dataset -> {bge_test_ans_emb.shape}")

Training Dataset


Batches:   0%|          | 0/13 [00:00<?, ?it/s]

Created question embedings using BGE
##############################


Batches:   0%|          | 0/13 [00:00<?, ?it/s]

Created answer embedings using BGE
##############################
Shape of Embeddings for Questions using BGE model in Training Dataset -> (396, 1024)
Shape of Embeddings for Answers using BGE model  in Training Dataset-> (396, 1024)

##################################################
Test Dataset


Batches:   0%|          | 0/17 [00:00<?, ?it/s]

Created question embedings using BGE for Test Dataset
##############################


Batches:   0%|          | 0/17 [00:00<?, ?it/s]

Created answer embedings using BGE for Test Dataset
##############################
Shape of Embeddings for Questions using Mini-LM model in Test Dataset -> (514, 1024)
Shape of Embeddings for Answers using Mini-LM model in Test Dataset -> (515, 1024)
CPU times: user 46 s, sys: 77.4 ms, total: 46 s
Wall time: 46 s


In [30]:
def get_train_predictions(train_df: pd.DataFrame,
                    question_embeddings: np.ndarray,
                    ans_embeddings: np.ndarray) -> List:
    """
    Get predictions by finding the candidate answer with the highest cosine similarity to each question.

    Args:
    train_df (pd.DataFrame): DataFrame containing the questions, candidate answers, and answer IDs.
    question_embeddings (np.ndarray): Array of embeddings for each question in `train_df`.
    ans_embeddings (np.ndarray): Array of embeddings for each answer in `train_df`.

    Returns:
    List: A list of predicted answers, where each element is the candidate answer with the highest cosine similarity.
    """
    # Create the train_ans_dict from train_df DataFrame and ans_embeddings
    train_ans_dict = {}
    for idx, row in enumerate(tqdm(train_df.iterrows(), total=len(train_df))):
        train_ans_dict[str(row[1]['answer_id'])] = ans_embeddings[idx]

    # Predictions
    preds = []
    for idx, row in enumerate(tqdm(train_df.iterrows(), total=len(train_df))):
        sim = []
        for ca in row[1]["candidate_answers"]:  # Accessing the candidate_answers in the row
            cos_sim = util.cos_sim(question_embeddings[idx], train_ans_dict.get(str(ca), np.zeros_like(ans_embeddings[0])))  # Calculate cosine similarity
            sim.append(cos_sim.item())

        aidx = np.argmax(np.array(sim))  # Find the index of the candidate answer with the highest similarity
        preds.append(row[1]["candidate_answers"][aidx])  # Append the candidate answer with the highest similarity

    return preds

In [ ]:
%%time
minilm_predictions = get_train_predictions(train_dataset, minilm_train_q_emb, minilm_train_ans_emb)

  0%|          | 0/396 [00:00<?, ?it/s]

  0%|          | 0/396 [00:00<?, ?it/s]

CPU times: user 360 ms, sys: 2.63 ms, total: 363 ms
Wall time: 381 ms


In [ ]:
print(type(minilm_predictions))

len(minilm_predictions)

<class 'list'>


396

In [ ]:
%%time
bge_predictions = get_train_predictions(train_dataset, bge_train_q_embed, bge_train_ans_embed)

  0%|          | 0/396 [00:00<?, ?it/s]

  0%|          | 0/396 [00:00<?, ?it/s]

CPU times: user 349 ms, sys: 3.75 ms, total: 353 ms
Wall time: 369 ms


In [ ]:
minilm_preds = np.array(minilm_predictions)
acc = accuracy_score(train_dataset.answer_id.values.ravel(), minilm_preds.astype(int).ravel())
print(acc)

0.9292929292929293


In [ ]:
bge_preds = np.array(bge_predictions)
acc = accuracy_score(train_dataset.answer_id.values.ravel(), bge_preds.astype(int).ravel())
print(acc)

0.9292929292929293


In [29]:
def get_test_predictions(test_qs: pd.DataFrame,
                         test_ans: pd.DataFrame,
                         q_emb: np.ndarray,
                         ans_emb: np.ndarray) -> List:
    """
    Get test predictions by finding the candidate answer with the highest cosine similarity to each question.

    Args:
    test_qs (pd.DataFrame): DataFrame containing the test questions and candidate answers.
    test_ans (pd.DataFrame): DataFrame containing the test answers and their IDs.
    q_emb (np.ndarray): Array of embeddings for each question in `test_qs`.
    ans_emb (np.ndarray): Array of embeddings for each answer in `test_ans`.

    Returns:
    List: A list of predicted answers, where each element is the candidate answer with the highest cosine similarity.
    """
    # Create the test_ans_dict from test_ans DataFrame and ans_emb
    test_ans_dict = {}
    for idx, row in enumerate(tqdm(test_ans.iterrows(), total=len(test_ans))):
        test_ans_dict[str(row[1]['answer_id'])] = ans_emb[idx]

    # Predictions
    preds = []
    for idx, row in enumerate(tqdm(test_qs.iterrows(), total=len(test_qs))):
        sim = []
        for ca in row[1]["candidate_answers"]:  # Accessing the candidate_answers in the row
            cos_sim = util.cos_sim(q_emb[idx], test_ans_dict.get(str(ca), np.zeros_like(ans_emb[0])))  # Calculate cosine similarity
            sim.append(cos_sim.item())

        aidx = np.argmax(np.array(sim))  # Find the index of the candidate answer with the highest similarity
        preds.append(row[1]["candidate_answers"][aidx])  # Append the candidate answer with the highest similarity

    return preds

In [ ]:
%%time
minilm_test_predictions = get_test_predictions(test_questions_dataset, test_answers_dataset, minilm_test_q_emb, minilm_test_ans_emb)

  0%|          | 0/515 [00:00<?, ?it/s]

  0%|          | 0/514 [00:00<?, ?it/s]

CPU times: user 456 ms, sys: 5.88 ms, total: 462 ms
Wall time: 481 ms


In [ ]:
print(type(minilm_test_predictions))

len(minilm_test_predictions)

<class 'list'>


514

In [ ]:
bge_test_predictions = get_test_predictions(test_questions_dataset, test_answers_dataset, bge_test_q_emb, bge_test_ans_emb)

  0%|          | 0/515 [00:00<?, ?it/s]

  0%|          | 0/514 [00:00<?, ?it/s]

In [ ]:
len(bge_test_predictions)

514

In [ ]:
bge_preds = np.array(bge_test_predictions).astype(int)
bge_preds.shape

(514,)

In [ ]:
test_questions_dataset['predicted_answer_id'] = bge_preds

In [ ]:
test_questions_dataset.head()

question_id  \
0          707   
1       534450   
2       996163   
3       860215   
4       980124   

                                                                                                                                                            question  \
0                                                                                       How much of an effort would it be to use AWS instead of GCP for assignments?   
1                                                                                                           Can you talk about linear regression and regularization?   
2  Can you please explain the Python Black setup in Visual Studio Code? Also, can you explain good Python coding standards as you write docstrings and type strings?   
3                                                                                    How many portfolio projects apart from the course are needed for getting a job?   
4                                                                     Can you talk more about the final project? What should we be thinking about now to prepare us?   

                      course  year                         candidate_answers  predicted_answer_id  
0  Data Engineering Zoomcamp  2023   [336232, 337669, 258304, 47681, 767296]               767296  
1  Machine Learning Zoomcamp  2022   [231208, 282072, 86769, 573165, 138373]               231208  
2  Data Engineering Zoomcamp  2023   [571892, 816559, 47681, 337669, 336232]               571892  
3  Machine Learning Zoomcamp  2022  [643931, 988549, 918931, 235894, 608866]               988549  
4  Data Engineering Zoomcamp  2023   [384381, 337669, 258304, 47681, 747722]               384381

In [ ]:
test_questions_dataset[['question_id', 'predicted_answer_id']].to_csv('BGE_submission.csv', index=False)

In [13]:
## Langchain
# Cohere embeddings

cohere_model = CohereEmbeddings(cohere_api_key = COHERE_API_KEY, model = "embed-english-v3.0")

print(f"Cohere -> model is Ready")
print(30 * '#')

# Jina embeddings
jina_model = JinaEmbeddings(jina_api_key = JINA_API_KEY, model_name = "jina-embeddings-v2-base-en")
print(f"Jina -> model is Ready")
print(30 * '#')

# Mistral embeddings
mistral_model = MistralAIEmbeddings(mistral_api_key = MISTRAL_API_KEY, model = "mistral-embed")
print(f"Mistral -> model is Ready")
print(30 * '#')

together_model = TogetherEmbeddings(together_api_key = TOGETHER_API_KEY, model="togethercomputer/m2-bert-80M-8k-retrieval")
print(f"Together -> model is Ready")
print(30 * '#')

# Voyage embeddings
voyage_model = VoyageEmbeddings(voyage_api_key = VOYAGE_API_KEY, model = "voyage-01")
print(f"Voyage -> model is Ready")
print(30 * '#')

## LlamaIndex
# OpenAI embeddings
openai_model = OpenAIEmbeddings(openai_api_key = OPENAI_API_KEY, model = "text-embedding-3-large")
print(f"OPENAI-> model is Ready")
print(30 * '#')

print("All Embeddings Models Ready!")

Cohere -> model is Ready
##############################
Jina -> model is Ready
##############################
Mistral -> model is Ready
##############################
Together -> model is Ready
##############################
Voyage -> model is Ready
##############################
OPENAI-> model is Ready
##############################
All Embeddings Models Ready!


In [14]:
def get_embedding(model, text: str):
  embedding = model.embed_query(text)
  return embedding

## COHERE - DID NOT WORK

In [53]:
%%time
cohere_train_q_embed = train_dataset['question'].apply(lambda x: get_embedding(cohere_model, x)).values

KeyboardInterrupt: 

In [ ]:
%%time
cohere_train_ans_embed = train_dataset['answer'].apply(lambda x: get_embedding(cohere_model, x)).values

In [ ]:
%%time
cohere_test_q_emb = test_questions_dataset['question'].apply(lambda x: get_embedding(cohere_model, x)).values

In [ ]:
%%time
cohere_test_ans_emb = test_answers_dataset['answer'].apply(lambda x: get_embedding(cohere_model, x)).values

In [52]:
print(f"Shape of Embeddings for Questions using Cohere model in Training Dataset -> {cohere_train_q_embed.shape}, {len(cohere_train_q_embed[0])}")
print(f"Shape of Embeddings for Answers using Cohere model  in Training Dataset-> {cohere_train_ans_embed.shape}, {len(cohere_train_ans_embed[0])}")
print(f"Shape of Embeddings for Questions using Cohere model in Test Dataset -> {cohere_test_q_emb.shape}, {len(cohere_test_q_emb[0])}")
print(f"Shape of Embeddings for Answers using Cohere model  in Test Dataset-> {cohere_test_ans_emb.shape}, {len(cohere_test_ans_emb[0])}")

NameError: name 'cohere_train_q_embed' is not defined

In [ ]:
cohere_predictions = get_train_predictions(train_dataset, cohere_train_q_embed, cohere_train_ans_embed)

In [ ]:
cohere_preds = np.array(cohere_predictions)
acc = accuracy_score(train_dataset.answer_id.values.ravel(), cohere_preds.astype(int).ravel())
print(acc)

In [ ]:
%%time
cohere_test_predictions = get_test_predictions(test_questions_dataset, test_answers_dataset, cohere_test_q_emb, cohere_test_ans_emb)

In [ ]:
cohere_preds = np.array(cohere_test_predictions).astype(int)
cohere_preds.shape

In [ ]:
test_questions_dataset.columns

Index(['question_id', 'question', 'course', 'year', 'candidate_answers', 'predicted_answer_id'], dtype='object')

In [ ]:
test_questions_dataset = test_questions_dataset.drop(columns='predicted_answer_id')

In [ ]:
test_questions_dataset.head()

question_id  \
0          707   
1       534450   
2       996163   
3       860215   
4       980124   

                                                                                                                                                            question  \
0                                                                                       How much of an effort would it be to use AWS instead of GCP for assignments?   
1                                                                                                           Can you talk about linear regression and regularization?   
2  Can you please explain the Python Black setup in Visual Studio Code? Also, can you explain good Python coding standards as you write docstrings and type strings?   
3                                                                                    How many portfolio projects apart from the course are needed for getting a job?   
4                                                                     Can you talk more about the final project? What should we be thinking about now to prepare us?   

                      course  year                         candidate_answers  
0  Data Engineering Zoomcamp  2023   [336232, 337669, 258304, 47681, 767296]  
1  Machine Learning Zoomcamp  2022   [231208, 282072, 86769, 573165, 138373]  
2  Data Engineering Zoomcamp  2023   [571892, 816559, 47681, 337669, 336232]  
3  Machine Learning Zoomcamp  2022  [643931, 988549, 918931, 235894, 608866]  
4  Data Engineering Zoomcamp  2023   [384381, 337669, 258304, 47681, 747722]

In [ ]:
test_questions_dataset['predicted_answer_id'] = cohere_preds

In [ ]:
test_questions_dataset[['question_id', 'predicted_answer_id']].to_csv('Cohere_submission.csv', index=False)

## JINA

In [ ]:
%%time
jina_train_q_embed = train_dataset['question'].apply(lambda x: get_embedding(jina_model, x)).values

CPU times: user 938 ms, sys: 89 ms, total: 1.03 s
Wall time: 1min 41s


In [ ]:
%%time
jina_train_ans_embed = train_dataset['answer'].apply(lambda x: get_embedding(jina_model, x)).values

CPU times: user 795 ms, sys: 80.7 ms, total: 876 ms
Wall time: 1min 41s


In [ ]:
%%time
jina_test_q_emb = test_questions_dataset['question'].apply(lambda x: get_embedding(jina_model, x)).values

CPU times: user 1.08 s, sys: 109 ms, total: 1.19 s
Wall time: 2min 10s


In [ ]:
%%time
jina_test_ans_emb = test_answers_dataset['answer'].apply(lambda x: get_embedding(jina_model, x)).values

CPU times: user 1.05 s, sys: 104 ms, total: 1.15 s
Wall time: 2min 12s


In [ ]:
print(f"Shape of Embeddings for Questions using Jina model in Training Dataset -> {jina_train_q_embed.shape}, {len(jina_train_q_embed[0])}")
print(f"Shape of Embeddings for Answers using Jina model in Training Dataset -> {jina_train_ans_embed.shape}, {len(jina_train_ans_embed[0])}")
print(f"Shape of Embeddings for Questions using Jina model in Test Dataset -> {jina_test_q_emb.shape}, {len(jina_test_q_emb[0])}")
print(f"Shape of Embeddings for Answers using Jina model in Test Dataset -> {jina_test_ans_emb.shape}, {len(jina_test_ans_emb[0])}")

Shape of Embeddings for Questions using Jina model in Training Dataset -> (396,), 768
Shape of Embeddings for Answers using Jina model in Training Dataset -> (396,), 768
Shape of Embeddings for Questions using Jina model in Test Dataset -> (514,), 768
Shape of Embeddings for Answers using Jina model in Test Dataset -> (515,), 768


In [32]:
def get_train_predictions(train_df: pd.DataFrame,
                          question_embeddings: np.ndarray,
                          ans_embeddings: np.ndarray) -> List:
    """
    Get predictions by finding the candidate answer with the highest cosine similarity to each question.

    Args:
    train_df (pd.DataFrame): DataFrame containing the questions, candidate answers, and answer IDs.
    question_embeddings (np.ndarray): Array of embeddings for each question in `train_df`.
    ans_embeddings (np.ndarray): Array of embeddings for each answer in `train_df`.

    Returns:
    List: A list of predicted answers, where each element is the candidate answer with the highest cosine similarity.
    """
    # Create the train_ans_dict from train_df DataFrame and ans_embeddings
    train_ans_dict = {}
    for idx, row in enumerate(tqdm(train_df.iterrows(), total=len(train_df))):
        train_ans_dict[str(row[1]['answer_id'])] = torch.tensor(ans_embeddings[idx], dtype=torch.float32)  # Convert to tensor with dtype float32

    # Predictions
    preds = []
    for idx, row in enumerate(tqdm(train_df.iterrows(), total=len(train_df))):
        sim = []
        question_embed = torch.tensor(question_embeddings[idx], dtype=torch.float32)  # Convert to tensor with dtype float32
        for ca in row[1]["candidate_answers"]:  # Accessing the candidate_answers in the row
            answer_embed = train_ans_dict.get(str(ca), torch.zeros_like(question_embed))  # Get the answer embedding
            cos_sim = util.cos_sim(question_embed, answer_embed)  # Calculate cosine similarity
            sim.append(cos_sim.item())

        aidx = np.argmax(np.array(sim))  # Find the index of the candidate answer with the highest similarity
        preds.append(row[1]["candidate_answers"][aidx])  # Append the candidate answer with the highest similarity

    return preds

In [ ]:
# For training dataset
jina_predictions = get_train_predictions(train_dataset, jina_train_q_embed, jina_train_ans_embed)
jina_preds = np.array(jina_predictions)
jina_acc = accuracy_score(train_dataset.answer_id.values.ravel(), jina_preds.astype(int).ravel())
print('Jina Model Training Accuracy:', jina_acc)

  0%|          | 0/396 [00:00<?, ?it/s]

  0%|          | 0/396 [00:00<?, ?it/s]

Jina Model Training Accuracy: 0.9242424242424242


In [ ]:
# For test dataset
jina_test_predictions = get_test_predictions(test_questions_dataset, test_answers_dataset, jina_test_q_emb, jina_test_ans_emb)
jina_test_preds = np.array(jina_test_predictions).astype(int)
print('Jina Test Predictions Shape:', jina_test_preds.shape)

  0%|          | 0/515 [00:00<?, ?it/s]

  0%|          | 0/514 [00:00<?, ?it/s]

Jina Test Predictions Shape: (514,)


In [ ]:
test_questions_dataset['predicted_answer_id'] = jina_test_preds

In [ ]:
test_questions_dataset[['question_id', 'predicted_answer_id']].to_csv('Jina_submission.csv', index=False)

## TOGETHER AI - DID NOT WORK

In [54]:
%%time
together_train_q_embed = train_dataset['question'].apply(lambda x: get_embedding(together_model, x)).values

RateLimitError: Too many requests received. Please pace your requests.

In [ ]:
%%time
together_train_ans_embed = train_dataset['answer'].apply(lambda x: get_embedding(together_model, x)).values

In [ ]:
%%time
together_test_q_emb = test_questions_dataset['question'].apply(lambda x: get_embedding(together_model, x)).values

In [ ]:
%%time
together_test_ans_emb = test_answers_dataset['answer'].apply(lambda x: get_embedding(together_model, x)).values

In [ ]:
print(f"Shape of Embeddings for Questions using Together model in Training Dataset -> {together_train_q_embed.shape}, {len(together_train_q_embed)}")
print(f"Shape of Embeddings for Answers using Together model in Training Dataset -> {together_train_ans_embed.shape}, {len(together_train_ans_embed)}")
print(f"Shape of Embeddings for Questions using Together model in Test Dataset -> {together_test_q_emb.shape}, {len(together_test_q_emb)}")
print(f"Shape of Embeddings for Answers using Together model in Test Dataset -> {together_test_ans_emb.shape}, {len(together_test_ans_emb)}")

## VOYAGE AI

In [18]:
%%time
voyage_train_q_embed = train_dataset['question'].apply(lambda x: get_embedding(voyage_model, x)).values

CPU times: user 27.7 s, sys: 468 ms, total: 28.2 s
Wall time: 2min 59s


In [19]:
%%time
voyage_train_ans_embed = train_dataset['answer'].apply(lambda x: get_embedding(voyage_model, x)).values

CPU times: user 27.8 s, sys: 472 ms, total: 28.3 s
Wall time: 3min 10s


In [20]:
%%time
voyage_test_q_emb = test_questions_dataset['question'].apply(lambda x: get_embedding(voyage_model, x)).values

CPU times: user 35.3 s, sys: 530 ms, total: 35.8 s
Wall time: 3min 50s


In [21]:
%%time
voyage_test_ans_emb = test_answers_dataset['answer'].apply(lambda x: get_embedding(voyage_model, x)).values

CPU times: user 36.6 s, sys: 714 ms, total: 37.3 s
Wall time: 4min 3s


In [23]:
print(f"Shape of Embeddings for Questions using Voyage model in Training Dataset -> {voyage_train_q_embed.shape}, {len(voyage_train_q_embed[0])}")
print(f"Shape of Embeddings for Answers using Voyage model in Training Dataset -> {voyage_train_ans_embed.shape}, {len(voyage_train_ans_embed[0])}")
print(f"Shape of Embeddings for Questions using Voyage model in Test Dataset -> {voyage_test_q_emb.shape}, {len(voyage_test_q_emb[0])}")
print(f"Shape of Embeddings for Answers using Voyage model in Test Dataset -> {voyage_test_ans_emb.shape}, {len(voyage_test_ans_emb[0])}")

Shape of Embeddings for Questions using Voyage model in Training Dataset -> (396,), 1024
Shape of Embeddings for Answers using Voyage model in Training Dataset -> (396,), 1024
Shape of Embeddings for Questions using Voyage model in Test Dataset -> (514,), 1024
Shape of Embeddings for Answers using Voyage model in Test Dataset -> (515,), 1024


In [36]:
import json

def get_train_predictions(train_df: pd.DataFrame,
                          question_embeddings: np.ndarray,
                          ans_embeddings: np.ndarray) -> List:
    """
    Get predictions by finding the candidate answer with the highest cosine similarity to each question.

    Args:
    train_df (pd.DataFrame): DataFrame containing the questions, candidate answers, and answer IDs.
    question_embeddings (np.ndarray): Array of embeddings for each question in `train_df`.
    ans_embeddings (np.ndarray): Array of embeddings for each answer in `train_df`.

    Returns:
    List: A list of predicted answers, where each element is the candidate answer with the highest cosine similarity.
    """
    # Create the train_ans_dict from train_df DataFrame and ans_embeddings
    train_ans_dict = {}
    for idx, row in enumerate(tqdm(train_df.iterrows(), total=len(train_df))):
        train_ans_dict[str(row[1]['answer_id'])] = torch.tensor(ans_embeddings[idx], dtype=torch.float32)  # Convert to tensor with dtype float32

    # Predictions
    preds = []
    for idx, row in enumerate(tqdm(train_df.iterrows(), total=len(train_df))):
        sim = []
        question_embed = torch.tensor(question_embeddings[idx], dtype=torch.float32)  # Convert to tensor with dtype float32
        candidate_answers = row[1]["candidate_answers"]

        # Ensure candidate_answers is a list (convert if it's a string representation of a list)
        if isinstance(candidate_answers, str):
            candidate_answers = json.loads(candidate_answers.replace("'", '"'))  # Convert string to list

        for ca in candidate_answers:  # Accessing the candidate_answers in the row
            answer_embed = train_ans_dict.get(str(ca), torch.zeros_like(question_embed))  # Get the answer embedding
            cos_sim = util.cos_sim(question_embed, answer_embed)  # Calculate cosine similarity
            sim.append(cos_sim.item())

        aidx = np.argmax(np.array(sim))  # Find the index of the candidate answer with the highest similarity
        preds.append(candidate_answers[aidx])  # Append the candidate answer with the highest similarity

    return preds


In [37]:
# For training dataset
voyage_predictions = get_train_predictions(train_dataset, voyage_train_q_embed, voyage_train_ans_embed)
voyage_preds = np.array(voyage_predictions)
voyage_acc = accuracy_score(train_dataset.answer_id.values.ravel(), voyage_preds.astype(int).ravel())
print('Voyage Model Training Accuracy:', voyage_acc)

  0%|          | 0/396 [00:00<?, ?it/s]

  0%|          | 0/396 [00:00<?, ?it/s]

Voyage Model Training Accuracy: 0.9242424242424242


In [41]:
import json
from typing import List
import numpy as np
from sentence_transformers import util
from tqdm import tqdm
import pandas as pd
import torch

def get_test_predictions(test_qs: pd.DataFrame,
                         test_ans: pd.DataFrame,
                         q_emb: np.ndarray,
                         ans_emb: np.ndarray) -> List:
    """
    Get test predictions by finding the candidate answer with the highest cosine similarity to each question.

    Args:
    test_qs (pd.DataFrame): DataFrame containing the test questions and candidate answers.
    test_ans (pd.DataFrame): DataFrame containing the test answers and their IDs.
    q_emb (np.ndarray): Array of embeddings for each question in `test_qs`.
    ans_emb (np.ndarray): Array of embeddings for each answer in `test_ans`.

    Returns:
    List: A list of predicted answers, where each element is the candidate answer with the highest cosine similarity.
    """
    # Create the test_ans_dict from test_ans DataFrame and ans_emb
    test_ans_dict = {}
    for idx, row in enumerate(tqdm(test_ans.iterrows(), total=len(test_ans))):
        test_ans_dict[str(row[1]['answer_id'])] = torch.tensor(ans_emb[idx], dtype=torch.float32)  # Convert to tensor with dtype float32

    # Predictions
    preds = []
    for idx, row in enumerate(tqdm(test_qs.iterrows(), total=len(test_qs))):
        sim = []
        question_embed = torch.tensor(q_emb[idx], dtype=torch.float32).unsqueeze(0)  # Convert to 2D tensor with dtype float32
        candidate_answers = row[1]["candidate_answers"]

        # If candidate_answers is a string representation of a list, convert it to an actual list
        if isinstance(candidate_answers, str):
            candidate_answers = json.loads(candidate_answers.replace("'", '"'))  # Convert string to list

        for ca in candidate_answers:  # Accessing the candidate_answers in the row
            answer_embed = test_ans_dict.get(str(ca), torch.zeros_like(question_embed))  # Get the answer embedding
            cos_sim = util.cos_sim(question_embed, answer_embed)  # Calculate cosine similarity
            sim.append(cos_sim.item())

        aidx = np.argmax(np.array(sim))  # Find the index of the candidate answer with the highest similarity

        # Ensure we are appending individual integer IDs or strings that represent integers
        selected_answer = candidate_answers[aidx]
        if isinstance(selected_answer, str) and selected_answer.isdigit():
            selected_answer = int(selected_answer)  # Convert to int if it's a digit string

        preds.append(selected_answer)

    return preds

In [42]:
# For test dataset
voyage_test_predictions = get_test_predictions(test_questions_dataset, test_answers_dataset, voyage_test_q_emb, voyage_test_ans_emb)
voyage_test_preds = np.array(voyage_test_predictions).astype(int)
print('Voyage Test Predictions Shape:', voyage_test_preds.shape)

100%|██████████| 514/514 [00:00<00:00, 1557.89it/s]

Voyage Test Predictions Shape: (514,)


In [43]:
test_questions_dataset['predicted_answer_id'] = voyage_test_preds
test_questions_dataset[['question_id', 'predicted_answer_id']].to_csv('Voyage_submission.csv', index=False)

In [45]:
test_questions_dataset.head()

question_id  \
0          707   
1       534450   
2       996163   
3       860215   
4       980124   

                                                                                                                                                            question  \
0                                                                                       How much of an effort would it be to use AWS instead of GCP for assignments?   
1                                                                                                           Can you talk about linear regression and regularization?   
2  Can you please explain the Python Black setup in Visual Studio Code? Also, can you explain good Python coding standards as you write docstrings and type strings?   
3                                                                                    How many portfolio projects apart from the course are needed for getting a job?   
4                                                                     Can you talk more about the final project? What should we be thinking about now to prepare us?   

                      course  year                                   candidate_answers  \
0  Data Engineering Zoomcamp  2023   ['336232', '337669', '258304', '47681', '767296']   
1  Machine Learning Zoomcamp  2022   ['231208', '282072', '86769', '573165', '138373']   
2  Data Engineering Zoomcamp  2023   ['571892', '816559', '47681', '337669', '336232']   
3  Machine Learning Zoomcamp  2022  ['643931', '988549', '918931', '235894', '608866']   
4  Data Engineering Zoomcamp  2023   ['384381', '337669', '258304', '47681', '747722']   

   predicted_answer_id  
0               767296  
1               231208  
2               571892  
3               988549  
4               384381

In [46]:
test_questions_dataset = test_questions_dataset.drop(columns='predicted_answer_id')

In [47]:
test_questions_dataset.head()

question_id  \
0          707   
1       534450   
2       996163   
3       860215   
4       980124   

                                                                                                                                                            question  \
0                                                                                       How much of an effort would it be to use AWS instead of GCP for assignments?   
1                                                                                                           Can you talk about linear regression and regularization?   
2  Can you please explain the Python Black setup in Visual Studio Code? Also, can you explain good Python coding standards as you write docstrings and type strings?   
3                                                                                    How many portfolio projects apart from the course are needed for getting a job?   
4                                                                     Can you talk more about the final project? What should we be thinking about now to prepare us?   

                      course  year                                   candidate_answers  
0  Data Engineering Zoomcamp  2023   ['336232', '337669', '258304', '47681', '767296']  
1  Machine Learning Zoomcamp  2022   ['231208', '282072', '86769', '573165', '138373']  
2  Data Engineering Zoomcamp  2023   ['571892', '816559', '47681', '337669', '336232']  
3  Machine Learning Zoomcamp  2022  ['643931', '988549', '918931', '235894', '608866']  
4  Data Engineering Zoomcamp  2023   ['384381', '337669', '258304', '47681', '747722']

## OPENAI

In [ ]:
%%time

openai_train_q_embed = train_dataset['question'].apply(lambda x: get_embedding(openai_model, x)).values

In [25]:
%%time

openai_train_ans_embed = train_dataset['answer'].apply(lambda x: get_embedding(openai_model, x)).values

CPU times: user 6.13 s, sys: 283 ms, total: 6.42 s
Wall time: 1min 20s


In [26]:
%%time

openai_test_q_emb = test_questions_dataset['question'].apply(lambda x: get_embedding(openai_model, x)).values


CPU times: user 4.87 s, sys: 309 ms, total: 5.18 s
Wall time: 1min 39s


In [27]:
%%time

openai_test_ans_emb = test_answers_dataset['answer'].apply(lambda x: get_embedding(openai_model, x)).values

CPU times: user 7.03 s, sys: 351 ms, total: 7.38 s
Wall time: 1min 45s


In [28]:
print(f"Shape of Embeddings for Questions using OpenAI model in Training Dataset -> {openai_train_q_embed.shape}, {len(openai_train_q_embed[0])}")
print(f"Shape of Embeddings for Answers using OpenAI model in Training Dataset -> {openai_train_ans_embed.shape}, {len(openai_train_ans_embed[0])}")
print(f"Shape of Embeddings for Questions using OpenAI model in Test Dataset -> {openai_test_q_emb.shape}, {len(openai_test_q_emb[0])}")
print(f"Shape of Embeddings for Answers using OpenAI model in Test Dataset -> {openai_test_ans_emb.shape}, {len(openai_test_ans_emb[0])}")

Shape of Embeddings for Questions using OpenAI model in Training Dataset -> (396,), 3072
Shape of Embeddings for Answers using OpenAI model in Training Dataset -> (396,), 3072
Shape of Embeddings for Questions using OpenAI model in Test Dataset -> (514,), 3072
Shape of Embeddings for Answers using OpenAI model in Test Dataset -> (515,), 3072


In [48]:
# For training dataset
openai_predictions = get_train_predictions(train_dataset, openai_train_q_embed, openai_train_ans_embed)
openai_preds = np.array(openai_predictions)
openai_acc = accuracy_score(train_dataset.answer_id.values.ravel(), openai_preds.astype(int).ravel())
print('OpenAI Model Training Accuracy:', openai_acc)

100%|██████████| 396/396 [00:00<00:00, 1175.38it/s]

OpenAI Model Training Accuracy: 0.9393939393939394


In [49]:
# For test dataset
openai_test_predictions = get_test_predictions(test_questions_dataset, test_answers_dataset, openai_test_q_emb, openai_test_ans_emb)
openai_test_preds = np.array(openai_test_predictions).astype(int)
print('OpenAI Test Predictions Shape:', openai_test_preds.shape)

100%|██████████| 514/514 [00:00<00:00, 1175.34it/s]

OpenAI Test Predictions Shape: (514,)


In [50]:
test_questions_dataset['predicted_answer_id'] = openai_test_preds

In [51]:
test_questions_dataset[['question_id', 'predicted_answer_id']].to_csv('Openai_submission.csv', index=False)

## TESTING API's

In [ ]:
# text_cohere = get_embedding(cohere_model, "How are you?")
# print(f"Embedding Dimension using Cohere Model: {len(text_cohere)}")

Embedding Dimension using Cohere Model: 1024


In [ ]:
text_jina = get_embedding(jina_model, "How are you?")
print(f"Embedding Dimension using Jina Model: {len(text_jina)}")

Embedding Dimension using Cohere Model: 768


In [ ]:
# text_mistral = embed_text(mistral_model, "How are you?")
# print(f"Embedding Dimension using Mistral Model: {len(text_mistral)}") # DID NOT WORK -> ERROR CODE: 429

In [ ]:
text_openai = get_embedding(openai_model, "How are you?")
print(f"Embedding Dimension using OpenAI Model: {len(text_openai)}")

Embedding Dimension using OpenAI Model: 3072


In [ ]:
text_together = get_embedding(together_model, "How are you?")
print(f"Embedding Dimension using Together Model: {len(text_together)}")

Embedding Dimension using Together Model: 768


In [ ]:
text_voyage = get_embedding(voyage_model, "How are you?")
print(f"Embedding Dimension using Voyage Model: {len(text_voyage)}")

Embedding Dimension using Voyage Model: 1024
